In [0]:
spark

In [0]:
display(dbutils.fs.mounts())

mountPoint source encryptionType /databricks-datasets databricks-datasets /Volumes UnityCatalogVolumes /databricks/mlflow-tracking databricks/mlflow-tracking /databricks-results databricks-results /databricks/mlflow-registry databricks/mlflow-registry /mnt/datalakeea44c854c651c494/bronze wasbs://bronze@datalakeea44c854c651c494.blob.core.windows.net /mnt/datalakeea44c854c651c494/landing-zone wasbs://landing-zone@datalakeea44c854c651c494.blob.core.windows.net /Volume DbfsReserved /mnt/datalakeea44c854c651c494/silver wasbs://silver@datalakeea44c854c651c494.blob.core.windows.net /volumes DbfsReserved / DatabricksRoot /volume DbfsReserved

In [0]:
# dbutils.fs.unmount('/mnt/datalakeea44c854c651c494/landing-zone')
# dbutils.fs.unmount('/mnt/datalakeea44c854c651c494/bronze')
dbutils.fs.unmount('/mnt/datalakeea44c854c651c494/silver')
dbutils.fs.unmount('/mnt/datalakeea44c854c651c494/gold')

---------------------------------------------------------------------------
ExecutionError                            Traceback (most recent call last)
File <command-3108921795436497>, line 3
      1 # dbutils.fs.unmount('/mnt/datalakeea44c854c651c494/landing-zone')
      2 # dbutils.fs.unmount('/mnt/datalakeea44c854c651c494/bronze')
----> 3 dbutils.fs.unmount('/mnt/datalakeea44c854c651c494/silver')
      4 dbutils.fs.unmount('/mnt/datalakeea44c854c651c494/gold')

File /databricks/python_shell/lib/dbruntime/dbutils.py:158, in prettify_exception_message.<locals>.f_with_exception_handling(*args, **kwargs)
    156 exc.__context__ = None
    157 exc.__cause__ = None
--> 158 raise exc

ExecutionError: An error occurred while calling o2004.unmount.
: java.rmi.RemoteException: java.lang.IllegalArgumentException: requirement failed: Directory not mounted: /mnt/datalakeea44c854c651c494/silver; nested exception is: 
	java.lang.IllegalArgumentException: requirement failed: Directory not mounted: 

In [0]:
storageAccountName = "datalakeea44c854c651c494"
storageAccountAccessKey = ""
sasToken = "sv=2024-11-04&ss=bfqt&srt=co&sp=rwdlacupyx&se=2025-06-22T20:53:54Z&st=2025-06-22T12:53:54Z&spr=https&sig=Hpb3PmZFNznLCM3GNOSOebgi%2BIcRHmU%2BigiiIPHGAVw%3D"

def mount_adls(blobContainerName):
    try:
      dbutils.fs.mount(
        source = "wasbs://{}@{}.blob.core.windows.net".format(blobContainerName, storageAccountName),
        mount_point = f"/mnt/{storageAccountName}/{blobContainerName}",
        #extra_configs = {'fs.azure.account.key.' + storageAccountName + '.blob.core.windows.net': storageAccountAccessKey}
        extra_configs = {'fs.azure.sas.' + blobContainerName + '.' + storageAccountName + '.blob.core.windows.net': sasToken}
      )
      print(f"Montagem bem-sucedida: {blobContainerName}")
    except Exception as e:
      print(f"Falha na montagem de {blobContainerName}:", e)

In [0]:
# mount_adls('landing-zone')
# mount_adls('bronze')
mount_adls('silver')
# mount_adls('gold')

Montagem bem-sucedida: silver


In [0]:
display(dbutils.fs.mounts())

mountPoint source encryptionType /databricks-datasets databricks-datasets /Volumes UnityCatalogVolumes /databricks/mlflow-tracking databricks/mlflow-tracking /databricks-results databricks-results /databricks/mlflow-registry databricks/mlflow-registry /mnt/datalakeea44c854c651c494/bronze wasbs://bronze@datalakeea44c854c651c494.blob.core.windows.net /mnt/datalakeea44c854c651c494/landing-zone wasbs://landing-zone@datalakeea44c854c651c494.blob.core.windows.net /Volume DbfsReserved /mnt/datalakeea44c854c651c494/silver wasbs://silver@datalakeea44c854c651c494.blob.core.windows.net /volumes DbfsReserved / DatabricksRoot /volume DbfsReserved

In [0]:
display(dbutils.fs.ls(f"/mnt/{storageAccountName}/silver"))

path name size modificationTime dbfs:/mnt/datalakeea44c854c651c494/silver/circuits/ circuits/ 0 0 dbfs:/mnt/datalakeea44c854c651c494/silver/constructor_results/ constructor_results/ 0 0 dbfs:/mnt/datalakeea44c854c651c494/silver/constructor_standings/ constructor_standings/ 0 0 dbfs:/mnt/datalakeea44c854c651c494/silver/constructors/ constructors/ 0 0 dbfs:/mnt/datalakeea44c854c651c494/silver/driver_standings/ driver_standings/ 0 0 dbfs:/mnt/datalakeea44c854c651c494/silver/drivers/ drivers/ 0 0 dbfs:/mnt/datalakeea44c854c651c494/silver/lap_times/ lap_times/ 0 0 dbfs:/mnt/datalakeea44c854c651c494/silver/pit_stops/ pit_stops/ 0 0 dbfs:/mnt/datalakeea44c854c651c494/silver/qualifying/ qualifying/ 0 0 dbfs:/mnt/datalakeea44c854c651c494/silver/races/ races/ 0 0 dbfs:/mnt/datalakeea44c854c651c494/silver/results/ results/ 0 0 dbfs:/mnt/datalakeea44c854c651c494/silver/seasons/ seasons/ 0 0 dbfs:/mnt/datalakeea44c854c651c494/silver/sprint_results/ sprint_results/ 0 0 dbfs:/mnt/datalakeea44c854c651c494/silver/status/ status/ 0 0

In [0]:
df_circuits              = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/circuits")
df_constructor_results   = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/constructor_results")
df_constructor_standings = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/constructor_standings")
df_constructors          = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/constructors")
df_driver_standings      = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/driver_standings")
df_drivers               = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/drivers")
df_lap_times             = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/lap_times")
df_pit_stops             = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/pit_stops")
df_qualifying            = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/qualifying")
df_races                 = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/races")
df_results               = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/results")
df_seasons               = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/seasons")
df_sprint_results        = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/sprint_results")
df_status                = spark.read.format('delta').load(f"/mnt/{storageAccountName}/silver/status")


In [0]:
%sql
-- USE SCHEMA gold;
drop table if exists dim_driver;

In [0]:
dbutils.fs.rm("dbfs:/mnt/datalakeea44c854c651c494/gold/dim_driver", recurse=True)


True

In [0]:

%sql
USE spark_catalog.default;

CREATE TABLE IF NOT EXISTS dim_driver (
    SK_DRIVER BIGINT GENERATED BY DEFAULT AS IDENTITY,
    IDENTIFIER_DRIVER INTEGER,
    REFERENCE_DRIVER VARCHAR(100),
    FORENAME VARCHAR(50),
    NATIONALITY VARCHAR(50)
)
USING delta
LOCATION 'dbfs:/mnt/datalakeea44c854c651c494/gold/dim_driver'

In [0]:
%sql
DESCRIBE TABLE EXTENDED dim_driver



col_name data_type comment SK_DRIVER bigint null IDENTIFIER_DRIVER int null REFERENCE_DRIVER varchar(100) null FORENAME varchar(50) null NATIONALITY varchar(50) null # Detailed Table Information Catalog spark_catalog Database default Table dim_driver Created Time Sun Jun 22 14:51:56 UTC 2025 Last Access UNKNOWN Created By Spark 3.5.0 Type EXTERNAL Location dbfs:/mnt/datalakeea44c854c651c494/gold/dim_driver Provider delta Owner root Table Properties [delta.enableDeletionVectors=true,delta.feature.deletionVectors=supported,delta.feature.identityColumns=supported,delta.minReaderVersion=3,delta.minWriterVersion=7]

In [0]:

df_drivers.createOrReplaceTempView("drivers")


In [0]:
%sql
  SELECT 
    try_cast(IDENTIFIER_DRIVER AS INT) AS IDENTIFIER_DRIVER,
    REFERENCE_DRIVER,
    FORENAME,
    NATIONALITY
  FROM drivers

IDENTIFIER_DRIVER REFERENCE_DRIVER FORENAME NATIONALITY 1 hamilton Lewis British 2 heidfeld Nick German 3 rosberg Nico German 4 alonso Fernando Spanish 5 kovalainen Heikki Finnish 6 nakajima Kazuki Japanese 7 bourdais Sébastien French 8 raikkonen Kimi Finnish 9 kubica Robert Polish 10 glock Timo German 11 sato Takuma Japanese 12 piquet_jr Nelson Brazilian 13 massa Felipe Brazilian 14 coulthard David British 15 trulli Jarno Italian 16 sutil Adrian German 17 webber Mark Australian 18 button Jenson British 19 davidson Anthony British 20 vettel Sebastian German 21 fisichella Giancarlo Italian 22 barrichello Rubens Brazilian 23 ralf_schumacher Ralf German 24 liuzzi Vitantonio Italian 25 wurz Alexander Austrian 26 speed Scott American 27 albers Christijan Dutch 28 markus_winkelhock Markus German 29 yamamoto Sakon Japanese 30 michael_schumacher Michael German 31 montoya Juan Colombian 32 klien Christian Austrian 33 monteiro Tiago Portuguese 34 ide Yuji Japanese 35 villeneuve Jacques Canadian 36 montagny Franck French 37 rosa Pedro Spanish 38 doornbos Robert Dutch 39 karthikeyan Narain Indian 40 friesacher Patrick Austrian 41 zonta Ricardo Brazilian 42 pizzonia Antônio Brazilian 43 matta Cristiano Brazilian 44 panis Olivier French 45 pantano Giorgio Italian 46 bruni Gianmaria Italian 47 baumgartner Zsolt Hungarian 48 gene Marc Spanish 49 frentzen Heinz-Harald German 50 verstappen Jos Dutch 51 wilson Justin British 52 firman Ralph Irish 53 kiesa Nicolas Danish 54 burti Luciano Brazilian 55 alesi Jean French 56 irvine Eddie British 57 hakkinen Mika Finnish 58 marques Tarso Brazilian 59 bernoldi Enrique Brazilian 60 mazzacane Gastón Argentine 61 enge Tomáš Czech 62 yoong Alex Malaysian 63 salo Mika Finnish 64 diniz Pedro Brazilian 65 herbert Johnny British 66 mcnish Allan British 67 buemi Sébastien Swiss 68 takagi Toranosuke Japanese 69 badoer Luca Italian 70 zanardi Alessandro Italian 71 damon_hill Damon British 72 sarrazin Stéphane French 73 rosset Ricardo Brazilian 74 tuero Esteban Argentine 75 nakano Shinji Japanese 76 magnussen Jan Danish 77 berger Gerhard Austrian 78 larini Nicola Italian 79 katayama Ukyo Japanese 80 sospiri Vincenzo Italian 81 morbidelli Gianni Italian 82 fontana Norberto Argentine 83 lamy Pedro Portuguese 84 brundle Martin British 85 montermini Andrea Italian 86 lavaggi Giovanni Italian 87 blundell Mark British 88 suzuki Aguri Japanese 89 inoue Taki Japanese 90 moreno Roberto Brazilian 91 wendlinger Karl Austrian 92 gachot Bertrand Belgian 93 schiattarella Domenico Italian 94 martini Pierluigi Italian 95 mansell Nigel British 96 boullion Jean-Christophe French 97 papis Massimiliano Italian 98 deletraz Jean-Denis Swiss 99 tarquini Gabriele Italian 100 comas Érik French 101 brabham David Australian 102 senna Ayrton Brazilian 103 bernard Éric French 104 fittipaldi Christian Brazilian 105 alboreto Michele Italian 106 beretta Olivier Monegasque 107 ratzenberger Roland Austrian 108 belmondo Paul French 109 lehto Jyrki Finnish 110 cesaris Andrea Italian 111 gounon Jean-Marc French 112 alliot Philippe French 113 adams Philippe Belgian 114 dalmas Yannick French 115 noda Hideki Japanese 116 lagorce Franck French 117 prost Alain French 118 warwick Derek British 119 patrese Riccardo Italian 120 barbazza Fabrizio Italian 121 andretti Michael American 122 capelli Ivan Italian 123 boutsen Thierry Belgian 124 apicella Marco Italian 125 naspetti Emanuele Italian 126 toshio_suzuki Toshio Japanese 127 gugelmin Maurício Brazilian 128 poele Eric Belgian 129 grouillard Olivier French 130 chiesa Andrea Swiss 131 modena Stefano Italian 132 amati Giovanna Italian 133 caffi Alex Italian 134 bertaggia Enrico Italian 135 mccarthy Perry British 136 lammers Jan Dutch 137 piquet Nelson Brazilian 138 satoru_nakajima Satoru Japanese 139 pirro Emanuele Italian 140 johansson Stefan Swedish 141 bailey Julian British 142 chaves Pedro Portuguese 143 bartels Michael German 144 hattori Naoki Japanese 145 nannini Alessandro Italian 146 schneider Bernd G

In [0]:
%sql
SELECT * FROM dim_driver

SK_DRIVER IDENTIFIER_DRIVER REFERENCE_DRIVER FORENAME NATIONALITY 1 1 hamilton Lewis British 2 2 heidfeld Nick German 3 3 rosberg Nico German 4 4 alonso Fernando Spanish 5 5 kovalainen Heikki Finnish 6 6 nakajima Kazuki Japanese 7 7 bourdais Sébastien French 8 8 raikkonen Kimi Finnish 9 9 kubica Robert Polish 10 10 glock Timo German 11 11 sato Takuma Japanese 12 12 piquet_jr Nelson Brazilian 13 13 massa Felipe Brazilian 14 14 coulthard David British 15 15 trulli Jarno Italian 16 16 sutil Adrian German 17 17 webber Mark Australian 18 18 button Jenson British 19 19 davidson Anthony British 20 20 vettel Sebastian German 21 21 fisichella Giancarlo Italian 22 22 barrichello Rubens Brazilian 23 23 ralf_schumacher Ralf German 24 24 liuzzi Vitantonio Italian 25 25 wurz Alexander Austrian 26 26 speed Scott American 27 27 albers Christijan Dutch 28 28 markus_winkelhock Markus German 29 29 yamamoto Sakon Japanese 30 30 michael_schumacher Michael German 31 31 montoya Juan Colombian 32 32 klien Christian Austrian 33 33 monteiro Tiago Portuguese 34 34 ide Yuji Japanese 35 35 villeneuve Jacques Canadian 36 36 montagny Franck French 37 37 rosa Pedro Spanish 38 38 doornbos Robert Dutch 39 39 karthikeyan Narain Indian 40 40 friesacher Patrick Austrian 41 41 zonta Ricardo Brazilian 42 42 pizzonia Antônio Brazilian 43 43 matta Cristiano Brazilian 44 44 panis Olivier French 45 45 pantano Giorgio Italian 46 46 bruni Gianmaria Italian 47 47 baumgartner Zsolt Hungarian 48 48 gene Marc Spanish 49 49 frentzen Heinz-Harald German 50 50 verstappen Jos Dutch 51 51 wilson Justin British 52 52 firman Ralph Irish 53 53 kiesa Nicolas Danish 54 54 burti Luciano Brazilian 55 55 alesi Jean French 56 56 irvine Eddie British 57 57 hakkinen Mika Finnish 58 58 marques Tarso Brazilian 59 59 bernoldi Enrique Brazilian 60 60 mazzacane Gastón Argentine 61 61 enge Tomáš Czech 62 62 yoong Alex Malaysian 63 63 salo Mika Finnish 64 64 diniz Pedro Brazilian 65 65 herbert Johnny British 66 66 mcnish Allan British 67 67 buemi Sébastien Swiss 68 68 takagi Toranosuke Japanese 69 69 badoer Luca Italian 70 70 zanardi Alessandro Italian 71 71 damon_hill Damon British 72 72 sarrazin Stéphane French 73 73 rosset Ricardo Brazilian 74 74 tuero Esteban Argentine 75 75 nakano Shinji Japanese 76 76 magnussen Jan Danish 77 77 berger Gerhard Austrian 78 78 larini Nicola Italian 79 79 katayama Ukyo Japanese 80 80 sospiri Vincenzo Italian 81 81 morbidelli Gianni Italian 82 82 fontana Norberto Argentine 83 83 lamy Pedro Portuguese 84 84 brundle Martin British 85 85 montermini Andrea Italian 86 86 lavaggi Giovanni Italian 87 87 blundell Mark British 88 88 suzuki Aguri Japanese 89 89 inoue Taki Japanese 90 90 moreno Roberto Brazilian 91 91 wendlinger Karl Austrian 92 92 gachot Bertrand Belgian 93 93 schiattarella Domenico Italian 94 94 martini Pierluigi Italian 95 95 mansell Nigel British 96 96 boullion Jean-Christophe French 97 97 papis Massimiliano Italian 98 98 deletraz Jean-Denis Swiss 99 99 tarquini Gabriele Italian 100 100 comas Érik French 101 101 brabham David Australian 102 102 senna Ayrton Brazilian 103 103 bernard Éric French 104 104 fittipaldi Christian Brazilian 105 105 alboreto Michele Italian 106 106 beretta Olivier Monegasque 107 107 ratzenberger Roland Austrian 108 108 belmondo Paul French 109 109 lehto Jyrki Finnish 110 110 cesaris Andrea Italian 111 111 gounon Jean-Marc French 112 112 alliot Philippe French 113 113 adams Philippe Belgian 114 114 dalmas Yannick French 115 115 noda Hideki Japanese 116 116 lagorce Franck French 117 117 prost Alain French 118 118 warwick Derek British 119 119 patrese Riccardo Italian 120 120 barbazza Fabrizio Italian 121 121 andretti Michael American 122 122 capelli Ivan Italian 123 123 boutsen Thierry Belgian 124 124 apicella Marco Italian 125 125 naspetti Emanuele Italian 126 126 toshio_suzuki Toshio Japanese 127 127 gugelmin Maurício Brazilian 128 128 poele Eric Belgian 129 129 grouillard Olivier French 130 130 chiesa Andrea Swiss 131 131 moden

In [0]:
%sql
-- USE CATALOG ws_engenharis_dados;
-- USE SCHEMA gold;

WITH drivers_relacional AS (
  SELECT 
    try_cast(IDENTIFIER_DRIVER AS INT) AS IDENTIFIER_DRIVER,
    REFERENCE_DRIVER,
    FORENAME,
    NATIONALITY
  FROM drivers
)

MERGE INTO dim_driver AS d
USING drivers_relacional AS dr
ON d.IDENTIFIER_DRIVER = dr.IDENTIFIER_DRIVER

WHEN MATCHED AND (
     d.REFERENCE_DRIVER <> dr.REFERENCE_DRIVER OR
     d.FORENAME <> dr.FORENAME OR
     d.NATIONALITY <> dr.NATIONALITY
) THEN
  UPDATE SET 
    REFERENCE_DRIVER = dr.REFERENCE_DRIVER,
    FORENAME = dr.FORENAME,
    NATIONALITY = dr.NATIONALITY

WHEN NOT MATCHED THEN
  INSERT (IDENTIFIER_DRIVER, REFERENCE_DRIVER, FORENAME, NATIONALITY)
  VALUES (dr.IDENTIFIER_DRIVER, dr.REFERENCE_DRIVER, dr.FORENAME, dr.NATIONALITY);


num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 861 0 0 861

In [0]:
%sql
-- USE SCHEMA gold;
drop table if exists dim_circuits;

In [0]:
dbutils.fs.rm("dbfs:/mnt/datalakeea44c854c651c494/gold/dim_circuits", recurse=True)


True

In [0]:
%sql
USE spark_catalog.default;

CREATE TABLE IF NOT EXISTS dim_circuits (
    SK_CIRCUITS BIGINT GENERATED BY DEFAULT AS IDENTITY,
    IDENTIFIER_CIRCUIT INTEGER,
    REFERENCE_CIRCUIT VARCHAR(100),
    COUNTRY VARCHAR(50)
)
USING delta
LOCATION 'dbfs:/mnt/datalakeea44c854c651c494/gold/dim_circuits'

In [0]:
%sql
DESCRIBE TABLE EXTENDED dim_circuits

col_name data_type comment SK_CIRCUITS bigint null IDENTIFIER_CIRCUIT int null REFERENCE_CIRCUIT varchar(100) null COUNTRY varchar(50) null # Detailed Table Information Catalog spark_catalog Database default Table dim_circuits Created Time Sun Jun 22 14:36:58 UTC 2025 Last Access UNKNOWN Created By Spark 3.5.0 Type EXTERNAL Location dbfs:/mnt/datalakeea44c854c651c494/gold/dim_circuits Provider delta Owner root Table Properties [delta.enableDeletionVectors=true,delta.feature.deletionVectors=supported,delta.feature.identityColumns=supported,delta.minReaderVersion=3,delta.minWriterVersion=7]

In [0]:
df_circuits.createOrReplaceTempView("circuits")

In [0]:
%sql
  SELECT 
    try_cast(IDENTIFIER_CIRCUIT AS INT) AS IDENTIFIER_CIRCUIT,
    REFERENCE_CIRCUIT,
    COUNTRY
  FROM circuits

IDENTIFIER_CIRCUIT REFERENCE_CIRCUIT COUNTRY 1 albert_park Australia 2 sepang Malaysia 3 bahrain Bahrain 4 catalunya Spain 5 istanbul Turkey 6 monaco Monaco 7 villeneuve Canada 8 magny_cours France 9 silverstone UK 10 hockenheimring Germany 11 hungaroring Hungary 12 valencia Spain 13 spa Belgium 14 monza Italy 15 marina_bay Singapore 16 fuji Japan 17 shanghai China 18 interlagos Brazil 19 indianapolis USA 20 nurburgring Germany 21 imola Italy 22 suzuka Japan 80 vegas United States 24 yas_marina UAE 25 galvez Argentina 26 jerez Spain 27 estoril Portugal 28 okayama Japan 29 adelaide Australia 30 kyalami South Africa 31 donington UK 32 rodriguez Mexico 33 phoenix USA 34 ricard France 35 yeongam Korea 36 jacarepagua Brazil 37 detroit USA 38 brands_hatch UK 39 zandvoort Netherlands 40 zolder Belgium 41 dijon France 42 dallas USA 43 long_beach USA 44 las_vegas USA 45 jarama Spain 46 watkins_glen USA 47 anderstorp Sweden 48 mosport Canada 49 montjuic Spain 50 nivelles Belgium 51 charade France 52 tremblant Canada 53 essarts France 54 lemans France 55 reims France 56 george South Africa 57 zeltweg Austria 58 aintree UK 59 boavista Portugal 60 riverside USA 61 avus Germany 62 monsanto Portugal 63 sebring USA 64 ain-diab Morocco 65 pescara Italy 66 bremgarten Switzerland 67 pedralbes Spain 68 buddh India 69 americas USA 70 red_bull_ring Austria 71 sochi Russia 73 baku Azerbaijan 75 portimao Portugal 76 mugello Italy 77 jeddah Saudi Arabia 78 losail Qatar 79 miami USA

In [0]:
%sql
SELECT * FROM dim_circuits

SK_CIRCUITS IDENTIFIER_CIRCUIT REFERENCE_CIRCUIT COUNTRY 1 1 albert_park Australia 2 2 sepang Malaysia 3 3 bahrain Bahrain 4 4 catalunya Spain 5 5 istanbul Turkey 6 6 monaco Monaco 7 7 villeneuve Canada 8 8 magny_cours France 9 9 silverstone UK 10 10 hockenheimring Germany 11 11 hungaroring Hungary 12 12 valencia Spain 13 13 spa Belgium 14 14 monza Italy 15 15 marina_bay Singapore 16 16 fuji Japan 17 17 shanghai China 18 18 interlagos Brazil 19 19 indianapolis USA 20 20 nurburgring Germany 21 21 imola Italy 22 22 suzuka Japan 23 80 vegas United States 24 24 yas_marina UAE 25 25 galvez Argentina 26 26 jerez Spain 27 27 estoril Portugal 28 28 okayama Japan 29 29 adelaide Australia 30 30 kyalami South Africa 31 31 donington UK 32 32 rodriguez Mexico 33 33 phoenix USA 34 34 ricard France 35 35 yeongam Korea 36 36 jacarepagua Brazil 37 37 detroit USA 38 38 brands_hatch UK 39 39 zandvoort Netherlands 40 40 zolder Belgium 41 41 dijon France 42 42 dallas USA 43 43 long_beach USA 44 44 las_vegas USA 45 45 jarama Spain 46 46 watkins_glen USA 47 47 anderstorp Sweden 48 48 mosport Canada 49 49 montjuic Spain 50 50 nivelles Belgium 51 51 charade France 52 52 tremblant Canada 53 53 essarts France 54 54 lemans France 55 55 reims France 56 56 george South Africa 57 57 zeltweg Austria 58 58 aintree UK 59 59 boavista Portugal 60 60 riverside USA 61 61 avus Germany 62 62 monsanto Portugal 63 63 sebring USA 64 64 ain-diab Morocco 65 65 pescara Italy 66 66 bremgarten Switzerland 67 67 pedralbes Spain 68 68 buddh India 69 69 americas USA 70 70 red_bull_ring Austria 71 71 sochi Russia 72 73 baku Azerbaijan 73 75 portimao Portugal 74 76 mugello Italy 75 77 jeddah Saudi Arabia 76 78 losail Qatar 77 79 miami USA

In [0]:
%sql
-- USE CATALOG ws_engenharis_dados;
-- USE SCHEMA gold;

WITH circuits_relacional AS (
  SELECT 
    try_cast(IDENTIFIER_CIRCUIT AS INT) AS IDENTIFIER_CIRCUIT,
    REFERENCE_CIRCUIT,
    COUNTRY
  FROM circuits
)

MERGE INTO dim_circuits AS dc
USING circuits_relacional AS cr
ON dc.IDENTIFIER_CIRCUIT = cr.IDENTIFIER_CIRCUIT

WHEN MATCHED AND (
     dc.REFERENCE_CIRCUIT <> cr.REFERENCE_CIRCUIT OR
     dc.COUNTRY <> cr.COUNTRY
) THEN
  UPDATE SET 
    REFERENCE_CIRCUIT = cr.REFERENCE_CIRCUIT,
    COUNTRY = cr.COUNTRY

WHEN NOT MATCHED THEN
  INSERT (IDENTIFIER_CIRCUIT, REFERENCE_CIRCUIT, COUNTRY)
  VALUES (cr.IDENTIFIER_CIRCUIT, cr.REFERENCE_CIRCUIT, cr.COUNTRY);


num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 77 0 0 77

In [0]:
%sql
DESCRIBE DETAIL dim_circuits;


format id name description location createdAt lastModified partitionColumns clusteringColumns numFiles sizeInBytes properties minReaderVersion minWriterVersion tableFeatures statistics delta fdc3f1e2-7823-40cf-be12-5a2dc0790ba0 spark_catalog.default.dim_circuits null dbfs:/mnt/datalakeea44c854c651c494/gold/dim_circuits 2025-06-22T14:36:56.359Z 2025-06-22T14:37:24Z List() List() 1 3575 Map(delta.enableDeletionVectors -> true) 3 7 List(deletionVectors, identityColumns) Map(numRowsDeletedByDeletionVectors -> 0, numDeletionVectors -> 0)

In [0]:
%sql
-- USE SCHEMA gold;
drop table if exists dim_status;

In [0]:
dbutils.fs.rm("dbfs:/mnt/datalakeea44c854c651c494/gold/dim_status", recurse=True)


True

In [0]:
%sql
USE spark_catalog.default;

CREATE TABLE IF NOT EXISTS dim_status (
    SK_STATUS BIGINT GENERATED BY DEFAULT AS IDENTITY,
    IDENTIFIER_STATUS INTEGER,
    STATUS VARCHAR(20)
)
USING delta
LOCATION 'dbfs:/mnt/datalakeea44c854c651c494/gold/dim_status'

In [0]:
%sql
DESCRIBE TABLE EXTENDED dim_status

col_name data_type comment SK_STATUS bigint null IDENTIFIER_STATUS int null STATUS varchar(20) null # Detailed Table Information Catalog spark_catalog Database default Table dim_status Created Time Sun Jun 22 14:37:56 UTC 2025 Last Access UNKNOWN Created By Spark 3.5.0 Type EXTERNAL Location dbfs:/mnt/datalakeea44c854c651c494/gold/dim_status Provider delta Owner root Table Properties [delta.enableDeletionVectors=true,delta.feature.deletionVectors=supported,delta.feature.identityColumns=supported,delta.minReaderVersion=3,delta.minWriterVersion=7]

In [0]:
df_status.createOrReplaceTempView("status")

In [0]:
%sql
  SELECT 
    try_cast(IDENTIFIER_STATUS AS INT) AS IDENTIFIER_STATUS,
    STATUS
  FROM status

IDENTIFIER_STATUS STATUS 1 Finished 2 Disqualified 3 Accident 4 Collision 5 Engine 6 Gearbox 7 Transmission 8 Clutch 9 Hydraulics 10 Electrical 11 +1 Lap 12 +2 Laps 13 +3 Laps 14 +4 Laps 15 +5 Laps 16 +6 Laps 17 +7 Laps 18 +8 Laps 19 +9 Laps 20 Spun off 21 Radiator 22 Suspension 23 Brakes 24 Differential 25 Overheating 26 Mechanical 27 Tyre 28 Driver Seat 29 Puncture 30 Driveshaft 31 Retired 32 Fuel pressure 33 Front wing 34 Water pressure 35 Refuelling 36 Wheel 37 Throttle 38 Steering 39 Technical 40 Electronics 41 Broken wing 42 Heat shield fire 43 Exhaust 44 Oil leak 45 +11 Laps 46 Wheel rim 47 Water leak 48 Fuel pump 49 Track rod 50 +17 Laps 51 Oil pressure 128 +42 Laps 53 +13 Laps 54 Withdrew 55 +12 Laps 56 Engine fire 129 Engine misfire 58 +26 Laps 59 Tyre puncture 60 Out of fuel 61 Wheel nut 62 Not classified 63 Pneumatics 64 Handling 65 Rear wing 66 Fire 67 Wheel bearing 68 Physical 69 Fuel system 70 Oil line 71 Fuel rig 72 Launch control 73 Injured 74 Fuel 75 Power loss 76 Vibrations 77 107% Rule 78 Safety 79 Drivetrain 80 Ignition 81 Did not qualify 82 Injury 83 Chassis 84 Battery 85 Stalled 86 Halfshaft 87 Crankshaft 88 +10 Laps 89 Safety concerns 90 Not restarted 91 Alternator 92 Underweight 93 Safety belt 94 Oil pump 95 Fuel leak 96 Excluded 97 Did not prequalify 98 Injection 99 Distributor 100 Driver unwell 101 Turbo 102 CV joint 103 Water pump 104 Fatal accident 105 Spark plugs 106 Fuel pipe 107 Eye injury 108 Oil pipe 109 Axle 110 Water pipe 111 +14 Laps 112 +15 Laps 113 +25 Laps 114 +18 Laps 115 +22 Laps 116 +16 Laps 117 +24 Laps 118 +29 Laps 119 +23 Laps 120 +21 Laps 121 Magneto 122 +44 Laps 123 +30 Laps 124 +19 Laps 125 +46 Laps 126 Supercharger 127 +20 Laps 130 Collision damage 131 Power Unit 132 ERS 133 +49 Laps 134 +38 Laps 135 Brake duct 136 Seat 137 Damage 138 Debris 139 Illness 140 Undertray 141 Cooling system

In [0]:
%sql
SELECT * FROM dim_status

SK_STATUS IDENTIFIER_STATUS STATUS 1 1 Finished 2 2 Disqualified 3 3 Accident 4 4 Collision 5 5 Engine 6 6 Gearbox 7 7 Transmission 8 8 Clutch 9 9 Hydraulics 10 10 Electrical 11 11 +1 Lap 12 12 +2 Laps 13 13 +3 Laps 14 14 +4 Laps 15 15 +5 Laps 16 16 +6 Laps 17 17 +7 Laps 18 18 +8 Laps 19 19 +9 Laps 20 20 Spun off 21 21 Radiator 22 22 Suspension 23 23 Brakes 24 24 Differential 25 25 Overheating 26 26 Mechanical 27 27 Tyre 28 28 Driver Seat 29 29 Puncture 30 30 Driveshaft 31 31 Retired 32 32 Fuel pressure 33 33 Front wing 34 34 Water pressure 35 35 Refuelling 36 36 Wheel 37 37 Throttle 38 38 Steering 39 39 Technical 40 40 Electronics 41 41 Broken wing 42 42 Heat shield fire 43 43 Exhaust 44 44 Oil leak 45 45 +11 Laps 46 46 Wheel rim 47 47 Water leak 48 48 Fuel pump 49 49 Track rod 50 50 +17 Laps 51 51 Oil pressure 52 128 +42 Laps 53 53 +13 Laps 54 54 Withdrew 55 55 +12 Laps 56 56 Engine fire 57 129 Engine misfire 58 58 +26 Laps 59 59 Tyre puncture 60 60 Out of fuel 61 61 Wheel nut 62 62 Not classified 63 63 Pneumatics 64 64 Handling 65 65 Rear wing 66 66 Fire 67 67 Wheel bearing 68 68 Physical 69 69 Fuel system 70 70 Oil line 71 71 Fuel rig 72 72 Launch control 73 73 Injured 74 74 Fuel 75 75 Power loss 76 76 Vibrations 77 77 107% Rule 78 78 Safety 79 79 Drivetrain 80 80 Ignition 81 81 Did not qualify 82 82 Injury 83 83 Chassis 84 84 Battery 85 85 Stalled 86 86 Halfshaft 87 87 Crankshaft 88 88 +10 Laps 89 89 Safety concerns 90 90 Not restarted 91 91 Alternator 92 92 Underweight 93 93 Safety belt 94 94 Oil pump 95 95 Fuel leak 96 96 Excluded 97 97 Did not prequalify 98 98 Injection 99 99 Distributor 100 100 Driver unwell 101 101 Turbo 102 102 CV joint 103 103 Water pump 104 104 Fatal accident 105 105 Spark plugs 106 106 Fuel pipe 107 107 Eye injury 108 108 Oil pipe 109 109 Axle 110 110 Water pipe 111 111 +14 Laps 112 112 +15 Laps 113 113 +25 Laps 114 114 +18 Laps 115 115 +22 Laps 116 116 +16 Laps 117 117 +24 Laps 118 118 +29 Laps 119 119 +23 Laps 120 120 +21 Laps 121 121 Magneto 122 122 +44 Laps 123 123 +30 Laps 124 124 +19 Laps 125 125 +46 Laps 126 126 Supercharger 127 127 +20 Laps 128 130 Collision damage 129 131 Power Unit 130 132 ERS 131 133 +49 Laps 132 134 +38 Laps 133 135 Brake duct 134 136 Seat 135 137 Damage 136 138 Debris 137 139 Illness 138 140 Undertray 139 141 Cooling system

In [0]:
%sql
-- USE CATALOG ws_engenharis_dados;
-- USE SCHEMA gold;

WITH status_relacional AS (
  SELECT 
    try_cast(IDENTIFIER_STATUS AS INT) AS IDENTIFIER_STATUS,
    STATUS
  FROM status
)

MERGE INTO dim_status AS ds
USING status_relacional AS sr
ON ds.IDENTIFIER_STATUS = sr.IDENTIFIER_STATUS

WHEN MATCHED AND (
     ds.STATUS <> sr.STATUS
) THEN
  UPDATE SET 
    ds.STATUS = sr.STATUS

WHEN NOT MATCHED THEN
  INSERT (IDENTIFIER_STATUS, STATUS)
  VALUES (sr.IDENTIFIER_STATUS, sr.STATUS);


num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 139 0 0 139

In [0]:
%sql
-- USE SCHEMA gold;
drop table if exists dim_time;

In [0]:
dbutils.fs.rm("dbfs:/mnt/datalakeea44c854c651c494/gold/dim_time", recurse=True)


True

In [0]:
from pyspark.sql.functions import expr, date_format, row_number
from pyspark.sql.window import Window

# Define o intervalo de datas desejado
data_inicial = "1950-05-12"
data_final = "2024-12-07"

# Calcula o número de dias no intervalo
num_dias = spark.sql(f"SELECT datediff('{data_final}', '{data_inicial}')").collect()[0][0]

# Cria um DataFrame com uma coluna contendo uma sequência de datas
df_calendario = spark.range(0, num_dias + 1) \
    .selectExpr(f"date_add(to_date('{data_inicial}'), CAST(id AS INT)) AS Data")

# Extrai os componentes de data
df_tempo = df_calendario.selectExpr(
    "Data",
    "year(Data) AS Ano",
    "month(Data) AS Mes",
    "(CASE month(Data) \
        WHEN 1 THEN 'JANEIRO' \
        WHEN 2 THEN 'FEVEREIRO' \
        WHEN 3 THEN 'MARCO' \
        WHEN 4 THEN 'ABRIL' \
        WHEN 5 THEN 'MAIO' \
        WHEN 6 THEN 'JUNHO' \
        WHEN 7 THEN 'JULHO' \
        WHEN 8 THEN 'AGOSTO' \
        WHEN 9 THEN 'SETEMBRO' \
        WHEN 10 THEN 'OUTUBRO' \
        WHEN 11 THEN 'NOVEMBRO' \
        WHEN 12 THEN 'DEZEMBRO' \
    END) AS NomeMes",
    "day(Data) AS Dia",
    "(CASE dayofweek(Data) \
        WHEN 1 THEN 'DOMINGO' \
        WHEN 2 THEN 'SEGUNDA-FEIRA' \
        WHEN 3 THEN 'TERCA-FEIRA' \
        WHEN 4 THEN 'QUARTA-FEIRA' \
        WHEN 5 THEN 'QUINTA-FEIRA' \
        WHEN 6 THEN 'SEXTA-FEIRA' \
        WHEN 7 THEN 'SABADO' \
    END) AS NomeDiaSemana",
    "dayofweek(Data) AS NumeroDiaSemana"
)

# Define a janela para gerar o surrogate key
windowSpec = Window.orderBy("Data")

# Adiciona a coluna sk_time
df_tempo_sk = df_tempo.withColumn("sk_time", row_number().over(windowSpec))

# Exibe o DataFrame resultante
df_tempo_sk.display()

# Salva como tabela Delta
df_tempo_sk.write.option("path", f"/mnt/{storageAccountName}/gold/dim_time").saveAsTable("dim_time", format="delta")


Data Ano Mes NomeMes Dia NomeDiaSemana NumeroDiaSemana sk_time 1950-05-12 1950 5 MAIO 12 SEXTA-FEIRA 6 1 1950-05-13 1950 5 MAIO 13 SABADO 7 2 1950-05-14 1950 5 MAIO 14 DOMINGO 1 3 1950-05-15 1950 5 MAIO 15 SEGUNDA-FEIRA 2 4 1950-05-16 1950 5 MAIO 16 TERCA-FEIRA 3 5 1950-05-17 1950 5 MAIO 17 QUARTA-FEIRA 4 6 1950-05-18 1950 5 MAIO 18 QUINTA-FEIRA 5 7 1950-05-19 1950 5 MAIO 19 SEXTA-FEIRA 6 8 1950-05-20 1950 5 MAIO 20 SABADO 7 9 1950-05-21 1950 5 MAIO 21 DOMINGO 1 10 1950-05-22 1950 5 MAIO 22 SEGUNDA-FEIRA 2 11 1950-05-23 1950 5 MAIO 23 TERCA-FEIRA 3 12 1950-05-24 1950 5 MAIO 24 QUARTA-FEIRA 4 13 1950-05-25 1950 5 MAIO 25 QUINTA-FEIRA 5 14 1950-05-26 1950 5 MAIO 26 SEXTA-FEIRA 6 15 1950-05-27 1950 5 MAIO 27 SABADO 7 16 1950-05-28 1950 5 MAIO 28 DOMINGO 1 17 1950-05-29 1950 5 MAIO 29 SEGUNDA-FEIRA 2 18 1950-05-30 1950 5 MAIO 30 TERCA-FEIRA 3 19 1950-05-31 1950 5 MAIO 31 QUARTA-FEIRA 4 20 1950-06-01 1950 6 JUNHO 1 QUINTA-FEIRA 5 21 1950-06-02 1950 6 JUNHO 2 SEXTA-FEIRA 6 22 1950-06-03 1950 6 JUNHO 3 SABADO 7 23 1950-06-04 1950 6 JUNHO 4 DOMINGO 1 24 1950-06-05 1950 6 JUNHO 5 SEGUNDA-FEIRA 2 25 1950-06-06 1950 6 JUNHO 6 TERCA-FEIRA 3 26 1950-06-07 1950 6 JUNHO 7 QUARTA-FEIRA 4 27 1950-06-08 1950 6 JUNHO 8 QUINTA-FEIRA 5 28 1950-06-09 1950 6 JUNHO 9 SEXTA-FEIRA 6 29 1950-06-10 1950 6 JUNHO 10 SABADO 7 30 1950-06-11 1950 6 JUNHO 11 DOMINGO 1 31 1950-06-12 1950 6 JUNHO 12 SEGUNDA-FEIRA 2 32 1950-06-13 1950 6 JUNHO 13 TERCA-FEIRA 3 33 1950-06-14 1950 6 JUNHO 14 QUARTA-FEIRA 4 34 1950-06-15 1950 6 JUNHO 15 QUINTA-FEIRA 5 35 1950-06-16 1950 6 JUNHO 16 SEXTA-FEIRA 6 36 1950-06-17 1950 6 JUNHO 17 SABADO 7 37 1950-06-18 1950 6 JUNHO 18 DOMINGO 1 38 1950-06-19 1950 6 JUNHO 19 SEGUNDA-FEIRA 2 39 1950-06-20 1950 6 JUNHO 20 TERCA-FEIRA 3 40 1950-06-21 1950 6 JUNHO 21 QUARTA-FEIRA 4 41 1950-06-22 1950 6 JUNHO 22 QUINTA-FEIRA 5 42 1950-06-23 1950 6 JUNHO 23 SEXTA-FEIRA 6 43 1950-06-24 1950 6 JUNHO 24 SABADO 7 44 1950-06-25 1950 6 JUNHO 25 DOMINGO 1 45 1950-06-26 1950 6 JUNHO 26 SEGUNDA-FEIRA 2 46 1950-06-27 1950 6 JUNHO 27 TERCA-FEIRA 3 47 1950-06-28 1950 6 JUNHO 28 QUARTA-FEIRA 4 48 1950-06-29 1950 6 JUNHO 29 QUINTA-FEIRA 5 49 1950-06-30 1950 6 JUNHO 30 SEXTA-FEIRA 6 50 1950-07-01 1950 7 JULHO 1 SABADO 7 51 1950-07-02 1950 7 JULHO 2 DOMINGO 1 52 1950-07-03 1950 7 JULHO 3 SEGUNDA-FEIRA 2 53 1950-07-04 1950 7 JULHO 4 TERCA-FEIRA 3 54 1950-07-05 1950 7 JULHO 5 QUARTA-FEIRA 4 55 1950-07-06 1950 7 JULHO 6 QUINTA-FEIRA 5 56 1950-07-07 1950 7 JULHO 7 SEXTA-FEIRA 6 57 1950-07-08 1950 7 JULHO 8 SABADO 7 58 1950-07-09 1950 7 JULHO 9 DOMINGO 1 59 1950-07-10 1950 7 JULHO 10 SEGUNDA-FEIRA 2 60 1950-07-11 1950 7 JULHO 11 TERCA-FEIRA 3 61 1950-07-12 1950 7 JULHO 12 QUARTA-FEIRA 4 62 1950-07-13 1950 7 JULHO 13 QUINTA-FEIRA 5 63 1950-07-14 1950 7 JULHO 14 SEXTA-FEIRA 6 64 1950-07-15 1950 7 JULHO 15 SABADO 7 65 1950-07-16 1950 7 JULHO 16 DOMINGO 1 66 1950-07-17 1950 7 JULHO 17 SEGUNDA-FEIRA 2 67 1950-07-18 1950 7 JULHO 18 TERCA-FEIRA 3 68 1950-07-19 1950 7 JULHO 19 QUARTA-FEIRA 4 69 1950-07-20 1950 7 JULHO 20 QUINTA-FEIRA 5 70 1950-07-21 1950 7 JULHO 21 SEXTA-FEIRA 6 71 1950-07-22 1950 7 JULHO 22 SABADO 7 72 1950-07-23 1950 7 JULHO 23 DOMINGO 1 73 1950-07-24 1950 7 JULHO 24 SEGUNDA-FEIRA 2 74 1950-07-25 1950 7 JULHO 25 TERCA-FEIRA 3 75 1950-07-26 1950 7 JULHO 26 QUARTA-FEIRA 4 76 1950-07-27 1950 7 JULHO 27 QUINTA-FEIRA 5 77 1950-07-28 1950 7 JULHO 28 SEXTA-FEIRA 6 78 1950-07-29 1950 7 JULHO 29 SABADO 7 79 1950-07-30 1950 7 JULHO 30 DOMINGO 1 80 1950-07-31 1950 7 JULHO 31 SEGUNDA-FEIRA 2 81 1950-08-01 1950 8 AGOSTO 1 TERCA-FEIRA 3 82 1950-08-02 1950 8 AGOSTO 2 QUARTA-FEIRA 4 83 1950-08-03 1950 8 AGOSTO 3 QUINTA-FEIRA 5 84 1950-08-04 1950 8 AGOSTO 4 SEXTA-FEIRA 6 85 1950-08-05 1950 8 AGOSTO 5 SABADO 7 86 1950-08-06 1950 8 AGOSTO 6 DOMINGO 1 87 1950-08-07 1950 8 AGOSTO 7 SEGUNDA-FEIRA 2 88 1950-08-08 1950 8 AGOSTO 8 TERCA-FEIRA 3 89 1950-08-09 1950 8 AGOSTO 9 QUARTA-FEIRA 4 90 1950-08-10 1950 8 AGOSTO 10 QUINTA-FEIRA 5 91 1950-08-11 1950 8 AGOSTO 11 SEXTA-FEIRA 6 92

In [0]:
%sql
-- USE SCHEMA gold;
drop table if exists dim_races;

In [0]:
dbutils.fs.rm("dbfs:/mnt/datalakeea44c854c651c494/gold/dim_races", recurse=True)


True

In [0]:
%sql
USE spark_catalog.default;

CREATE TABLE IF NOT EXISTS dim_races (
  SK_RACES BIGINT GENERATED BY DEFAULT AS IDENTITY,
  SK_TIME BIGINT,
  IDENTIFIER_RACE INTEGER
)
USING delta
LOCATION 'dbfs:/mnt/datalakeea44c854c651c494/gold/dim_races';

In [0]:
%sql
DESCRIBE TABLE EXTENDED dim_races

col_name data_type comment SK_RACES bigint null SK_TIME bigint null IDENTIFIER_RACE int null # Detailed Table Information Catalog spark_catalog Database default Table dim_races Created Time Sun Jun 22 13:23:37 UTC 2025 Last Access UNKNOWN Created By Spark 3.5.0 Type EXTERNAL Location dbfs:/mnt/datalakeea44c854c651c494/gold/dim_races Provider delta Owner root Table Properties [delta.enableDeletionVectors=true,delta.feature.deletionVectors=supported,delta.feature.identityColumns=supported,delta.minReaderVersion=3,delta.minWriterVersion=7]

In [0]:
df_races.createOrReplaceTempView("races")

In [0]:
%sql
  SELECT 
    try_cast(IDENTIFIER_RACE AS INT) AS IDENTIFIER_RACE
  FROM races

IDENTIFIER_RACE 1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89 90 91 92 93 94 95 96 97 98 99 100 101 102 103 104 105 106 107 108 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125 126 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161 162 163 164 165 166 167 168 169 170 171 172 173 174 175 176 177 178 179 180 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196 197 198 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214 215 216 217 218 219 220 221 222 223 224 225 226 227 228 229 230 231 232 233 234 235 236 237 238 239 240 241 242 243 244 245 246 247 248 249 250 251 252 253 254 255 256 257 258 259 260 261 262 263 264 265 266 267 268 269 270 271 272 273 274 275 276 277 278 279 280 281 282 283 284 285 286 287 288 289 290 291 292 293 294 295 296 297 298 299 300 301 302 303 304 305 306 307 308 309 310 311 312 313 314 315 316 317 318 319 320 321 322 323 324 325 326 327 328 329 330 331 332 333 334 335 336 337 338 339 340 341 342 343 344 345 346 347 348 349 350 351 352 353 354 355 356 357 358 359 360 361 362 363 364 365 366 367 368 369 370 371 372 373 374 375 376 377 378 379 380 381 382 383 384 385 386 387 388 389 390 391 392 393 394 395 396 397 398 399 400 401 402 403 404 405 406 407 408 409 410 411 412 413 414 415 416 417 418 419 420 421 422 423 424 425 426 427 428 429 430 431 432 433 434 435 436 437 438 439 440 441 442 443 444 445 446 447 448 449 450 451 452 453 454 455 456 457 458 459 460 461 462 463 464 465 466 467 468 469 470 471 472 473 474 475 476 477 478 479 480 481 482 483 484 485 486 487 488 489 490 491 492 493 494 495 496 497 498 499 500 501 502 503 504 505 506 507 508 509 510 511 512 513 514 515 516 517 518 519 520 521 522 523 524 525 526 527 528 529 530 531 532 533 534 535 536 537 538 539 540 541 542 543 544 545 546 547 548 549 550 551 552 553 554 555 556 557 558 559 560 561 562 563 564 565 566 567 568 569 570 571 572 573 574 575 576 577 578 579 580 581 582 583 584 585 586 587 588 589 590 591 592 593 594 595 596 597 598 599 600 601 602 603 604 605 606 607 608 609 610 611 612 613 614 615 616 617 618 619 620 621 622 623 624 625 626 627 628 629 630 631 632 633 634 635 636 637 638 639 640 641 642 643 644 645 646 647 648 649 650 651 652 653 654 655 656 657 658 659 660 661 662 663 664 665 666 667 668 669 670 671 672 673 674 675 676 677 678 679 680 681 682 683 684 685 686 687 688 689 690 691 692 693 694 695 696 697 698 699 700 701 702 703 704 705 706 707 708 709 710 711 712 713 714 715 716 717 718 719 720 721 722 723 724 725 726 727 728 729 730 731 732 733 734 735 736 737 738 739 740 741 742 743 744 745 746 747 748 749 750 751 752 753 754 755 756 757 758 759 760 761 762 763 764 765 766 767 768 769 770 771 772 773 774 775 776 777 778 779 780 781 782 783 784 785 786 787 788 789 790 791 792 793 794 795 796 797 798 799 800 801 802 803 804 805 806 807 808 809 810 811 812 813 814 815 816 817 818 819 820 821 822 823 824 825 826 827 828 829 830 831 832 833 834 835 836 837 838 839 841 842 843 844 845 846 847 848 849 850 851 852 853 854 855 856 857 858 859 860 861 862 863 864 865 866 867 868 869 870 871 872 873 874 875 876 877 878 879 880 881 882 883 884 885 886 887 888 890 891 892 893 894 895 896 897 898 899 900 901 902 903 904 905 906 907 908 909 910 911 912 913 914 915 916 917 918 931 932 929 930 928 926 927 933 934 936 937 938 939 940 941 942 943 944 945 948 949 950 951 952 953 954 955 956 957 958 959 960 961 962 963 964 965 966 967 968 969 970 971 972 973 974 975 976 977 978 979 980 981 982 983 984 985 986 987 988 989 990 991 992 993 994 995 996 997 998 999 1000 1001 1002 1003 1004 1005 1006 1007 1008 1009 1010 1011 1012 1013 1014 1015 1016 1017 1018 1019 1020 1021 1022 1023 1024 1025 1026 1027 1028

In [0]:
%sql
SELECT * FROM dim_races

SK_RACES SK_TIME IDENTIFIER_RACE 1 2 833 2 10 834 3 19 835 4 24 836 5 38 837 6 52 838 7 115 839 8 381 825 9 384 826 10 402 827 11 416 828 12 429 829 13 444 830 14 493 831 15 535 832 16 738 817 17 750 818 18 773 819 19 787 820 20 800 821 21 815 822 22 829 823 23 850 824 24 983 808 25 1115 809 26 1123 810 27 1137 811 28 1151 812 29 1164 813 30 1179 814 31 1200 815 32 1221 816 33 1347 799 34 1481 800 35 1501 801 36 1515 802 37 1528 803 38 1543 804 39 1564 805 40 1578 806 41 1627 807 42 1711 792 43 1837 793 44 1845 794 45 1851 795 46 1865 796 47 1892 797 48 1949 798 49 2082 784 50 2194 785 51 2211 786 52 2215 787 53 2243 788 54 2256 789 55 2278 790 56 2306 791 57 2439 776 58 2565 777 59 2576 778 60 2614 779 61 2627 780 62 2642 781 63 2656 782 64 2677 783 65 2810 765 66 2929 766 67 2937 767 68 2941 768 69 2957 769 70 2978 770 71 2991 771 72 3006 772 73 3027 773 74 3041 774 75 3083 775 76 3286 756 77 3306 757 78 3307 758 79 3342 759 80 3355 760 81 3370 761 82 3391 762 83 3412 763 84 3502 764 85 3559 746 86 3671 747 87 3672 748 88 3679 749 89 3692 750 90 3706 751 91 3719 752 92 3748 753 93 3769 754 94 3846 755 95 4021 738 96 4029 739 97 4056 740 98 4070 741 99 4083 742 100 4105 743 101 4140 744 102 4168 745 103 4392 729 104 4406 730 105 4420 731 106 4441 732 107 4454 733 108 4469 734 109 4511 735 110 4532 736 111 4615 737 112 4763 719 113 4777 720 114 4791 721 115 4798 722 116 4818 723 117 4833 724 118 4868 725 119 4896 726 120 4917 727 121 4979 728 122 5113 709 123 5127 710 124 5148 711 125 5162 712 126 5175 713 127 5197 714 128 5218 715 129 5232 716 130 5260 717 131 5281 718 132 5349 699 133 5498 700 134 5512 701 135 5526 702 136 5539 703 137 5547 704 138 5561 705 139 5603 706 140 5624 707 141 5645 708 142 5855 690 143 5876 691 144 5897 692 145 5910 693 146 5918 694 147 5932 695 148 5960 696 149 5988 697 150 6009 698 151 6080 679 152 6205 680 153 6233 681 154 6247 682 155 6261 683 156 6274 684 157 6296 685 158 6317 686 159 6331 687 160 6352 688 161 6373 689 162 6444 667 163 6576 668 164 6590 669 165 6604 670 166 6618 671 167 6632 672 168 6645 673 169 6660 674 170 6695 675 171 6709 676 172 6723 677 173 6751 678 174 6869 656 175 6933 657 176 6947 658 177 6981 659 178 6996 660 179 7009 661 180 7024 662 181 7059 663 182 7072 664 183 7087 665 184 7101 666 185 7240 643 186 7283 644 187 7304 645 188 7332 646 189 7346 647 190 7360 648 191 7373 649 192 7388 650 193 7402 651 194 7423 652 195 7437 653 196 7451 654 197 7472 655 198 7604 632 199 7647 633 200 7682 634 201 7710 635 202 7724 636 203 7737 637 204 7752 638 205 7766 639 206 7787 640 207 7801 641 208 7815 642 209 7927 620 210 7968 621 211 8026 622 212 8039 623 213 8060 624 214 8088 625 215 8101 626 216 8116 627 217 8130 628 218 8158 629 219 8172 630 220 8186 631 221 8298 605 222 8312 606 223 8332 607 224 8389 608 225 8410 609 226 8424 610 227 8438 611 228 8452 612 229 8465 613 230 8480 614 231 8487 615 232 8501 616 233 8522 617 234 8536 618 235 8550 619 236 8648 590 237 8662 591 238 8724 592 239 8753 593 240 8767 594 241 8781 595 242 8795 596 243 8809 597 244 8823 598 245 8836 599 246 8851 600 247 8865 601 248 8886 602 249 8900 603 250 8914 604 251 9012 576 252 9026 577 253 9060 578 254 9117 579 255 9131 580 256 9145 581 257 9159 582 258 9173 583 259 9187 584 260 9200 585 261 9215 586 262 9229 587 263 9250 588 264 9278 589 265 9390 560 266 9431 561 267 9453 562 268 9488 563 269 9502 564 270 9516 565 271 9530 566 272 9551 567 273 9565 568 274 9579 569 275 9593 570 276 9607 571 277 9621 572 278 9642 573 279 9649 574 280 9663 575 281 9740 543 282 9754 544 283 9795 545 284 9824 546 285 9859 547 286 9873 548 287 9887 549 288 9901 550 289 9915 551 290 9928 552 291 9943 553 292 9957 554 293 9971 555 294 9985 556 295 10006 557 296 10013 558 297 10027 559 298 10111 527 299 10125 528 300 10159 529 301 10188 530 302 10223 531 303 10237 532 304 10251 533 305 10264 534 306 10279 535 307 10293 536 308 10307 537 309 10321 538 310 10335 539 311 10349 540 312 10370 541 313 10377 542 314 10482 512 315 

In [0]:
%sql

-- USE spark_catalog.default;

WITH races_data AS (
  SELECT
    IDENTIFIER_RACE,
    TO_DATE(DATE, 'yyyy-MM-dd') AS race_date
  FROM
    races
),

races_com_sk_time AS (
  SELECT
    r.IDENTIFIER_RACE,
    dt.sk_time
  FROM
    races_data r
  JOIN
    dim_time dt
  ON
    r.race_date = dt.Data
)

MERGE INTO dim_races dr
USING races_com_sk_time rst
ON dr.IDENTIFIER_RACE = rst.IDENTIFIER_RACE

WHEN NOT MATCHED THEN
  INSERT (SK_TIME, IDENTIFIER_RACE)
  VALUES (rst.sk_time, rst.IDENTIFIER_RACE)


num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 1124 0 0 1124

In [0]:
%sql
create table fat_crash_history (
   FK_RACES             int,
   FK_STATUS            int,
   FK_DRIVER            int,
   FK_CIRCUITS          int
)
USING delta
LOCATION '/mnt/datalakeea44c854c651c494/gold/fat_crash_history'

In [0]:
df_results.createOrReplaceTempView("results")
df_races.createOrReplaceTempView("races")
df_drivers.createOrReplaceTempView("drivers")
df_status.createOrReplaceTempView("status")
df_circuits.createOrReplaceTempView("circuits")

In [0]:
%sql
CREATE OR REPLACE TABLE fat_crash_history
USING delta
LOCATION '/mnt/datalakeea44c854c651c494/gold/fat_crash_history'
AS
SELECT
  d.SK_DRIVER     AS FK_DRIVER,
  s.SK_STATUS     AS FK_STATUS,
  r.SK_RACES      AS FK_RACES,
  c.SK_CIRCUITS   AS FK_CIRCUITS
FROM results res
JOIN races ra 
  ON res.IDENTIFIER_RACE = ra.IDENTIFIER_RACE
JOIN dim_driver d 
  ON res.IDENTIFIER_DRIVER = d.IDENTIFIER_DRIVER
JOIN dim_status s 
  ON res.IDENTIFIER_STATUS = s.IDENTIFIER_STATUS
JOIN dim_races r 
  ON res.IDENTIFIER_RACE = r.IDENTIFIER_RACE
JOIN dim_circuits c 
  ON ra.IDENTIFIER_CIRCUIT = c.IDENTIFIER_CIRCUIT
WHERE res.IDENTIFIER_STATUS IN (3, 4);


num_affected_rows num_inserted_rows

In [0]:
%sql
select * from fat_crash_history

FK_DRIVER FK_STATUS FK_RACES FK_CIRCUITS 9 4 786 1 10 3 786 1 14 4 786 1 17 4 786 1 18 4 786 1 19 4 786 1 20 4 786 1 21 4 786 1 10 4 787 2 18 4 788 3 22 4 789 4 5 3 789 4 7 4 789 4 12 4 789 4 16 4 789 4 20 4 789 4 6 4 790 5 21 4 790 5 16 4 791 6 3 3 791 6 12 3 791 6 14 3 791 6 7 4 791 6 6 3 792 7 8 4 792 7 1 4 792 7 18 4 793 8 20 4 794 9 14 4 794 9 22 4 795 10 16 3 797 12 4 4 797 12 21 3 799 14 8 3 800 15 16 3 800 15 12 3 800 15 14 4 801 16 15 4 802 17 12 3 803 18 14 4 803 18 25 4 769 1 14 4 769 1 27 3 769 1 16 4 770 2 18 4 771 3 26 4 771 3 25 4 772 4 16 3 773 6 24 3 773 6 15 3 774 7 24 3 774 7 9 3 774 7 16 3 774 7 26 3 774 7 14 4 775 19 22 4 775 19 23 4 775 19 19 4 776 8 15 4 776 8 24 4 776 8 26 3 777 9 23 4 778 20 19 3 779 11 29 3 779 11 14 3 781 14 11 4 783 16 20 4 783 16 17 4 783 16 4 3 783 16 25 4 783 16 16 3 784 17 5 3 785 18 29 4 785 18 21 4 785 18 8 3 752 2 24 3 753 1 30 3 753 1 32 3 753 1 15 3 753 1 3 3 753 1 13 3 753 1 27 3 754 21 14 3 755 20 24 3 755 20 3 3 757 6 26 3 758 9 23 3 758 9 17 3 758 9 11 3 759 7 35 3 759 7 31 3 759 7 3 3 759 7 27 3 759 7 33 3 760 19 11 3 760 19 18 3 760 19 8 3 760 19 2 3 760 19 31 3 760 19 17 3 760 19 26 3 760 19 32 3 760 19 36 3 760 19 35 3 762 10 3 3 762 10 8 4 763 11 24 4 763 11 17 3 763 11 8 4 764 5 33 4 764 5 13 4 766 17 17 3 767 22 2 3 768 18 17 4 768 18 3 4 768 18 30 3 732 1 2 3 732 1 21 4 733 2 17 4 733 2 21 3 735 21 24 3 737 6 40 3 737 6 14 3 737 6 8 3 738 20 17 3 738 20 18 3 739 7 14 3 744 11 32 3 744 11 31 4 747 13 42 4 747 13 15 3 747 13 30 3 747 13 11 3 747 13 21 3 747 13 42 3 748 18 14 3 748 18 42 3 749 22 15 3 749 22 31 3 749 22 39 3 750 17 43 3 717 21 30 4 719 6 4 3 719 6 14 4 719 6 21 4 719 6 32 3 719 6 23 4 720 20 43 4 720 20 13 3 721 7 32 4 722 19 13 4 722 19 45 4 722 19 46 4 722 19 15 3 724 9 44 3 724 9 18 4 727 13 47 4 727 13 17 4 727 13 11 4 727 13 46 4 727 13 45 4 727 13 45 3 728 14 44 4 728 14 23 4 729 17 32 4 729 17 14 4 730 22 22 4 730 22 17 4 731 18 52 3 698 1 22 3 698 1 17 3 700 18 18 3 700 18 30 3 700 18 31 3 700 18 42 3 700 18 44 4 700 18 14 4 702 4 15 4 702 4 8 4 702 4 49 3 704 6 15 3 705 7 17 3 709 10 23 3 709 10 49 3 709 10 22 3 709 10 8 3 709 10 52 3 709 10 44 3 712 19 17 3 712 19 23 3 712 19 22 4 712 19 22 4 681 1 23 4 681 1 21 4 681 1 13 4 681 1 2 4 681 1 18 4 681 1 44 4 681 1 66 4 681 1 13 4 683 18 2 4 686 70 11 4 686 70 59 4 686 70 13 3 687 6 44 4 687 6 18 4 687 6 8 4 687 6 62 3 687 6 66 3 687 6 31 4 689 20 14 4 689 20 21 3 689 20 44 3 691 8 13 4 695 14 37 4 695 14 13 3 697 22 23 4 664 1 35 4 664 1 31 4 666 18 50 4 666 18 22 4 666 18 37 4 668 4 49 4 668 4 49 3 670 6 2 4 670 6 31 3 671 7 2 4 671 7 56 4 671 7 21 4 671 7 15 4 674 9 44 4 674 9 41 4 675 10 2 4 675 10 37 4 675 10 37 4 677 13 2 4 677 13 56 4 677 13 54 4 677 13 15 4 678 14 8 4 680 22 55 4 680 22 55 4 651 4 37 4 651 4 65 4 652 20 25 4 652 20 56 4 652 20 23 4 652 20 15 4 652 20 23 4 654 7 35 4 654 7 37 4 654 7 2 4 656 70 55 4 656 70 30 4 656 70 15 4 656 70 21 4 656 70 64 4 657 10 55 4 657 10 30 4 657 10 21 4 657 10 15 4 659 13 65 4 660 14 22 4 660 14 14 4 660 14 15 4 660 14 49 4 660 14 37 4 660 14 15 4 661 19 37 4 663 2 2 4 663 2 64 4 663 2 48 4 631 1 15 4 631 1 71 4 631 1 64 4 632 18 71 4 632 18 71 4 634 6 55 4 636 7 15 4 636 7 35 4 640 10 64 4 640 10 69 4 643 14 48 4 643 14 70 4 644 20 25 4 644 20 64 4 644 20 71 4 645 2 23 4 615 1 76 4 615 1 35 4 617 25 65 4 617 25 56 4 619 4 21 4 619 4 49 4 620 6 63 3 621 7 55 4 621 7 15 4 621 7 21 4 624 70 55 4 624 70 64 4 624 70 63 4 624 70 68 4 624 70 21 4 627 13 30 4 627 13 57 4 627 13 25 4 627 13 65 4 627 13 22 4 627 13 44 4 627 13 63 4 627 13 73 4 627 13 68 4 630 22 74 4 630 22 35 4 598 1 56 4 598 1 65 4 598 1 76 3 599 18 21 4 600 25 30 4 600 25 14 4 600 25 75 4 601 21 71 4 601 21 57 4 602 6 71 4 602 6 23 3 604 7 35 3 604 7 56 3 604 7 14 4 605 8 49 4 606 9 65 3 607 10 64 3 607 10 49 4 607 10 56 4 607 10 76 3 608 11 23 4 610 14 65 4 610 14 56 4 611 70 55 4 611 70 79 4 612 20 21 4 612 20 23 4 612 20 30 4 614 26 55 4 582 1 84 4 582 1 65 4 582 1 84 4 584 2

In [0]:
%sql
create table fat_driver_history (
   FK_RACES             int,
   FK_DRIVER            int,
   FK_CIRCUITS          int,
   FASTESTLAPTIME       int
)
USING delta
LOCATION '/mnt/datalakeea44c854c651c494/gold/fat_driver_history'

In [0]:
%sql
CREATE OR REPLACE TABLE fat_driver_history
USING delta
LOCATION '/mnt/datalakeea44c854c651c494/gold/fat_driver_history'
AS
SELECT
  d.SK_DRIVER        AS FK_DRIVER,
  r.SK_RACES         AS FK_RACES,
  c.SK_CIRCUITS      AS FK_CIRCUITS,
  res.FASTESTLAPTIME AS FASTESTLAPTIME
FROM results res
JOIN races ra 
  ON res.IDENTIFIER_RACE = ra.IDENTIFIER_RACE
JOIN dim_driver d 
  ON res.IDENTIFIER_DRIVER = d.IDENTIFIER_DRIVER
JOIN dim_races r 
  ON res.IDENTIFIER_RACE = r.IDENTIFIER_RACE
JOIN dim_circuits c 
  ON ra.IDENTIFIER_CIRCUIT = c.IDENTIFIER_CIRCUIT
WHERE res.FASTESTLAPTIME IS NOT NULL;

num_affected_rows num_inserted_rows

In [0]:
%sql
select * from fat_driver_history

FK_DRIVER FK_RACES FK_CIRCUITS FASTESTLAPTIME 1 786 1 1:27.452 2 786 1 1:27.739 3 786 1 1:28.090 4 786 1 1:28.603 5 786 1 1:27.418 6 786 1 1:29.639 7 786 1 1:29.534 8 786 1 1:27.903 9 786 1 1:28.753 10 786 1 1:29.558 11 786 1 1:30.892 12 786 1 1:31.384 13 786 1 1:28.175 14 786 1 1:29.502 15 786 1 1:29.310 16 786 1 1:32.021 17 786 1 \N 18 786 1 \N 19 786 1 \N 20 786 1 \N 21 786 1 \N 22 786 1 1:28.736 8 787 2 1:35.405 9 787 2 1:35.921 5 787 2 1:35.922 15 787 2 1:36.068 1 787 2 1:35.462 2 787 2 1:35.366 17 787 2 1:36.696 4 787 2 1:36.288 14 787 2 1:36.206 18 787 2 1:35.715 12 787 2 1:36.956 21 787 2 1:36.962 22 787 2 1:36.693 3 787 2 1:36.782 19 787 2 1:38.171 11 787 2 1:38.504 6 787 2 1:37.711 20 787 2 1:36.870 13 787 2 1:35.914 16 787 2 1:40.330 10 787 2 \N 7 787 2 \N 13 788 3 1:33.600 8 788 3 1:33.709 9 788 3 1:33.775 2 788 3 1:33.565 5 788 3 1:33.193 15 788 3 1:34.204 17 788 3 1:34.305 3 788 3 1:34.072 10 788 3 1:34.807 4 788 3 1:35.194 22 788 3 1:34.855 21 788 3 1:35.057 1 788 3 1:35.520 6 788 3 1:35.433 7 788 3 1:35.333 19 788 3 1:35.324 11 788 3 1:35.891 14 788 3 1:35.351 16 788 3 1:35.442 12 788 3 1:35.129 18 788 3 1:36.125 20 788 3 \N 8 789 4 1:21.670 13 789 4 1:21.801 1 789 4 1:22.017 9 789 4 1:22.106 17 789 4 1:22.564 18 789 4 1:22.353 6 789 4 1:23.549 15 789 4 1:22.758 2 789 4 1:22.519 21 789 4 1:23.439 10 789 4 1:23.007 14 789 4 1:22.842 11 789 4 1:24.617 3 789 4 1:23.319 4 789 4 1:22.683 22 789 4 1:23.858 5 789 4 1:22.453 19 789 4 1:26.864 7 789 4 1:25.999 12 789 4 1:25.444 16 789 4 \N 20 789 4 \N 13 790 5 1:26.666 1 790 5 1:26.529 8 790 5 1:26.506 9 790 5 1:26.780 2 790 5 1:27.219 4 790 5 1:27.280 17 790 5 1:27.630 3 790 5 1:27.795 14 790 5 1:27.966 15 790 5 1:27.926 18 790 5 1:27.998 5 790 5 1:27.640 10 790 5 1:28.303 22 790 5 1:28.017 12 790 5 1:27.867 16 790 5 1:28.780 20 790 5 1:28.180 7 790 5 1:28.745 6 790 5 \N 21 790 5 \N 1 791 6 1:18.510 9 791 6 1:17.933 13 791 6 1:17.886 17 791 6 1:19.036 20 791 6 1:18.787 22 791 6 1:19.574 6 791 6 1:19.910 5 791 6 1:17.282 8 791 6 1:16.689 4 791 6 1:17.869 18 791 6 1:19.582 10 791 6 1:19.618 15 791 6 1:19.830 2 791 6 1:20.251 16 791 6 1:22.039 3 791 6 1:21.270 12 791 6 1:31.187 21 791 6 1:32.849 14 791 6 1:42.112 7 791 6 1:41.150 9 792 7 1:17.539 2 792 7 1:17.430 14 792 7 1:18.085 10 792 7 1:19.087 13 792 7 1:18.006 15 792 7 1:18.870 22 792 7 1:18.301 20 792 7 1:18.532 5 792 7 1:18.462 3 792 7 1:17.977 18 792 7 1:19.352 17 792 7 1:18.201 7 792 7 1:18.620 21 792 7 1:19.066 6 792 7 1:18.784 4 792 7 1:18.225 12 792 7 1:19.239 8 792 7 1:17.387 1 792 7 1:17.506 16 792 7 1:20.666 13 793 8 1:16.729 8 793 8 1:16.630 15 793 8 1:17.567 5 793 8 1:17.134 9 793 8 1:17.172 17 793 8 1:17.507 12 793 8 1:17.758 4 793 8 1:17.641 14 793 8 1:17.818 1 793 8 1:17.453 10 793 8 1:17.836 20 793 8 1:17.760 2 793 8 1:17.716 22 793 8 1:17.969 6 793 8 1:18.054 3 793 8 1:18.311 7 793 8 1:18.216 21 793 8 1:18.557 16 793 8 1:18.462 18 793 8 1:20.876 1 794 9 1:32.817 2 794 9 1:32.719 22 794 9 1:33.386 8 794 9 1:32.150 5 794 9 1:33.130 4 794 9 1:33.133 15 794 9 1:33.808 6 794 9 1:34.277 3 794 9 1:34.797 17 794 9 1:32.952 7 794 9 1:33.367 10 794 9 1:34.610 13 794 9 1:33.257 9 794 9 1:33.539 18 794 9 1:33.376 12 794 9 1:33.203 21 794 9 1:34.930 16 794 9 1:38.160 20 794 9 \N 14 794 9 \N 1 795 10 1:16.039 12 795 10 1:16.910 13 795 10 1:16.502 2 795 10 1:15.987 5 795 10 1:16.495 8 795 10 1:16.342 9 795 10 1:16.610 20 795 10 1:16.772 15 795 10 1:17.023 3 795 10 1:17.380 4 795 10 1:17.115 7 795 10 1:16.969 14 795 10 1:16.994 6 795 10 1:17.691 16 795 10 1:17.889 21 795 10 1:18.208 18 795 10 1:17.636 22 795 10 1:17.986 17 795 10 1:17.206 10 795 10 1:16.712 5 796 11 1:21.753 10 796 11 1:21.671 8 796 11 1:21.195 4 796 11 1:21.793 1 796 11 1:21.493 12 796 11 1:21.537 15 796 11 1:21.638 9 796 11 1:21.941 17 796 11 1:22.125 2 796 11 1:22.183 14 796 11 1:22.732 18 796 11 1:22.397 6 796 11 1:23.307 3 796 11 1:22.397 21 796 11 1:22.641 22 796 11 1:22.436 13 796 11 1:21.355 7 796 11 1:23.220 16 796 11 1:23.650 20 796 11 1: